## Suppl. Fig. 8 panel A external UMAPs

[NOTE]: before running this notebook, please preprocess external datasets using notebooks in `process_external_spatial_datasets`

In [31]:
# parameters
# umap
n_bootstraps = 10
n_neighbors = 20
min_dist = 0.1
metric = 'euclidean'

In [32]:
# imports
import os, sys, random, shutil, warnings
# Suppress all warnings
warnings.filterwarnings("ignore")
from pathlib import Path
import matplotlib.pyplot as plt
import pandas as pd
import umap
from collections import Counter
import plotly.io as pio
from tqdm.notebook import tqdm


plt.style.use('ggplot')
plt.rcParams['pdf.fonttype'] = 42

script_path = Path.cwd().parent.parent.parent.parent / "script"
data_path = Path.cwd().parent.parent.parent.parent / "data"
sys.path.append(str(script_path))
from pyseus.plotting import plotly_umap as pu
from utils.label_processing import attach_annotations


save_path = Path.cwd() / "output"
if not os.path.exists(save_path):
    os.makedirs(save_path)

### load external data

In [33]:
dataset_dirs = ["DLOPIT2024", "DIA-DOMs-2023", "hyperLOPITU2OS2018",
                "LOPITDCU2OS2018", "itzhak2016stcSILAC", "itzhak2016stcSILAC-NOC", "BioID2021-NMF"] 

In [34]:
datasets = {}
# loop over all datasets and load the fraction data
for dataset_dir in dataset_dirs:
    print(f"Load data for {dataset_dir}")
    dataset_dir_abs = Path.cwd() / "process_external_spatial_datasets" / dataset_dir

    if dataset_dir == "BioID2021-NMF": # for the BioID2021-NMF dataset, we need to load the fraction data from the xls file
        NMF_matrix_path = data_path / "external" / "BioID2021_NMF.xlsx"
        if not NMF_matrix_path.exists():
            raise FileNotFoundError(f"File {NMF_matrix_path} does not exist")
        NMF = pd.read_excel(NMF_matrix_path, sheet_name="A) rank profiles")
        new_col_level = ["metadata"] * 1 + ["sample"] * (NMF.shape[1] - 1)
        NMF.columns = pd.MultiIndex.from_arrays([new_col_level, NMF.columns])
        datasets[dataset_dir] = NMF
    else:
        if not dataset_dir_abs.exists(): # check if the dataset directory exists
            raise FileNotFoundError(f"Directory {dataset_dir_abs} does not exist")
        csv_path1 = dataset_dir_abs / "fraction" /"output" / "fraction_tables" / f'2024-07-16_fraction_table.csv'
        csv_path2 = dataset_dir_abs / "fraction" /"output" / "fraction_tables" / f'2024-07-27_fraction_table.csv'
        if not any([csv_path1.exists(), csv_path2.exists()]):
            raise FileNotFoundError(f"csv does not exist, tried:\n{csv_path1}\n{csv_path2}")
        existing_csv = next((path for path in [csv_path1, csv_path2] if os.path.exists(path)), None)
        fraction = pd.read_csv(existing_csv, header=[0, 1], index_col=0)

        if "NOC" in dataset_dir:
            csv_path = dataset_dir_abs / "fraction" /"output" / "fraction_tables" / f'2024-07-16_fraction_table_NOC.csv'
            if csv_path.exists():
                fraction = pd.read_csv(csv_path, header=[0, 1], index_col=0)

        datasets[dataset_dir] = fraction

Load data for DLOPIT2024
Load data for DIA-DOMs-2023
Load data for hyperLOPITU2OS2018
Load data for LOPITDCU2OS2018
Load data for itzhak2016stcSILAC
Load data for itzhak2016stcSILAC-NOC
Load data for BioID2021-NMF


In [35]:
# helper function
def translate_and_count(row, translation_dict):
    # Split the semicolon-separated values
    values = row.split(';')
    translated_values = []

    for value in values:
        # Attempt to translate the value directly
        translation = translation_dict.get(value)
        if translation is None:
            # If direct translation fails, try removing contents after a hyphen and translate again
            value_base = value.split('-')[0]
            translation = translation_dict.get(value_base, value_base)
        translated_values.append(translation)

    # Count the translations
    translation_counts = Counter(translated_values)
    # Find the highest count
    max_count = max(translation_counts.values())
    # Find all translations with the highest count
    most_common_translations = [k for k, v in translation_counts.items() if v == max_count]
    # Choose the shortest translation in case of ties
    most_common_translation = min(most_common_translations, key=len)
    
    return most_common_translation

In [37]:
# attach OrgIP annotation and Ground truth annotation to the datasets (for later visualization)

for dataset_dir in datasets:
    print(f"Attaching OrgIP annotations to {dataset_dir} (for visualization)")

    fraction = datasets[dataset_dir].copy() # 

    # load prot_ID to gene name mapping
    df = pd.read_csv(data_path / "external" / "HUMAN_9606_idmapping.dat", sep="\t", header=None)
    prot2gene = dict(zip(df[0], df[2]))

    # map protein IDs to gene names
    fraction = fraction.rename(columns={"Unnamed: 0": "Protein IDs"}, level=1)

    # map gene names
    if "Protein IDs" in fraction.columns.get_level_values(1):
        fraction["metadata", "Gene names remapped"] = fraction["metadata", "Protein IDs"].apply(translate_and_count, translation_dict=prot2gene)
    else:
        fraction = fraction.rename(columns={"gene": "Gene names remapped"}, level=1)

    # attach consensus graph annotation
    ground_truth_csv = Path.cwd().parent.parent.parent / "Fig2" / "panel_C" / "output" / "2023-10-21-imp5-for-figures_umap_table.csv"
    lookup_table = pd.read_csv(ground_truth_csv)
    to_df = fraction["metadata"].copy()
    list_of_cols_to_add = reversed(["consensus_graph_annnotation"])
    for c in list_of_cols_to_add:
        new_col_data = attach_annotations(from_df=lookup_table, to_df=to_df, anno_col=c, from_on="Gene_name_canonical", to_on="Gene names remapped")
        fraction["metadata", "consensus_graph_annnotation"] = new_col_data

    # attach ground truth
    ground_truth_csv = data_path / "external" / "curated_ground_truth_v9.0.csv"

    lookup_table = pd.read_csv(ground_truth_csv)
    to_df = fraction["metadata"].copy()
    list_of_cols_to_add = reversed(["compartment"])
    for c in list_of_cols_to_add:
        new_col_data = attach_annotations(from_df=lookup_table, to_df=to_df, anno_col=c, from_on="gene_name_canonical", to_on="Gene names remapped")
        fraction[("metadata", "curated_ground_truth_v9.0")] = new_col_data

    datasets[dataset_dir] = fraction

Attaching OrgIP annotations for DLOPIT2024 (for visualization)
Attaching OrgIP annotations for DIA-DOMs-2023 (for visualization)
Attaching OrgIP annotations for hyperLOPITU2OS2018 (for visualization)
Attaching OrgIP annotations for LOPITDCU2OS2018 (for visualization)
Attaching OrgIP annotations for itzhak2016stcSILAC (for visualization)
Attaching OrgIP annotations for itzhak2016stcSILAC-NOC (for visualization)
Attaching OrgIP annotations for BioID2021-NMF (for visualization)


### compute external umaps
computing umaps takes ~3 minutes for each dataset  
the default is to compute 10 umaps for each dataset, but you can change this by changing the `n_bootstraps` variable in the first cell of this notebook

In [38]:
umap_tables = {} # initialize a dictionary to store the UMAP embeddings for each dataset
umap_tables_last_seed = {}

for dataset in datasets:
    print(f"Computing UMAP embeddings for dataset: {dataset}")
    # df operations
    fraction = datasets[dataset]
    cols = list(fraction["sample"])
    meta_cols = list(fraction["metadata"])
    selected_samples = cols
    print(f"...the features used in computing UMAP are {sorted(selected_samples)}, count = {len(selected_samples)}")
    umap_table = fraction.droplevel(0, axis=1)[meta_cols + selected_samples].copy()
    # normalization and UMAP algorithm are not compatible with any NaN values, so drop them
    umap_table = umap_table.dropna(subset=selected_samples)
    quants = umap_table[selected_samples].copy()
    print(f"...the dimensions of the data used for UMAP are {quants.shape}")

    # scale the table
    scaled = pu.scale_table(matrix=quants, method='standard')

    # prepare output directory
    _output_dir = save_path / dataset 
    if not os.path.exists(_output_dir):
        os.makedirs(_output_dir)
    else:
        shutil.rmtree(_output_dir)
        os.makedirs(_output_dir)
        
    _output_dir = save_path / dataset / "UMAP" / "bootstraps"
    if not os.path.exists(_output_dir):
        os.makedirs(_output_dir)
    else:
        shutil.rmtree(_output_dir)
        os.makedirs(_output_dir)

    # compute UMAP embeddings and save them
    # loop through the bootstraps
    for _ in tqdm(range(n_bootstraps), desc="Bootstraps", total=n_bootstraps):
        UMAP_seed = random.randint(0, 10000)
        # calculate 2D UMAP embeddings
        fit = umap.UMAP(
            n_neighbors=n_neighbors, 
            min_dist=min_dist, 
            metric=metric, 
            random_state=UMAP_seed
        )
        u = fit.fit_transform(scaled)
        umap_table['umap_1'] = u[:, 0] 
        umap_table['umap_2'] = u[:, 1]

        # save umap embedding to dictionary, this will overwrite the previous embeddings, and only the last bootstrap will be saved
        umap_tables[dataset] = umap_table
        umap_tables_last_seed[dataset] = UMAP_seed

        # save umap embedding to csv file
        save_name = f"UMAP_embeddings_seed={UMAP_seed}.csv"
        umap_table.to_csv(os.path.join(_output_dir / save_name), index=False)

Computing UMAP embeddings for dataset: DLOPIT2024
...the features used in computing UMAP are ['126', '127C', '127N', '128C', '128N', '129C', '129N', '130N'], count = 8
...the dimensions of the data used for UMAP are (5314, 8)


Bootstraps:   0%|          | 0/10 [00:00<?, ?it/s]

Computing UMAP embeddings for dataset: DIA-DOMs-2023
...the features used in computing UMAP are ['01K', '03K', '06K', '12K', '24K', '80K'], count = 6
...the dimensions of the data used for UMAP are (7443, 6)


Bootstraps:   0%|          | 0/10 [00:00<?, ?it/s]

Computing UMAP embeddings for dataset: hyperLOPITU2OS2018
...the features used in computing UMAP are ['X126', 'X127C', 'X127N', 'X128C', 'X128N', 'X129C', 'X129N', 'X130C', 'X130N', 'X131'], count = 10
...the dimensions of the data used for UMAP are (4883, 10)


...

Bootstraps:   0%|          | 0/10 [00:00<?, ?it/s]

Computing UMAP embeddings for dataset: itzhak2016stcSILAC-NOC
...the features used in computing UMAP are ['03K', '06K', '12K', '24K', '80K', 'NOC_cytosol', 'NOC_nuclear', 'NOC_organelle'], count = 8
...the dimensions of the data used for UMAP are (4928, 8)


Bootstraps:   0%|          | 0/10 [00:00<?, ?it/s]

Computing UMAP embeddings for dataset: BioID2021-NMF
...the features used in computing UMAP are ['rank 1', 'rank 10', 'rank 11', 'rank 12', 'rank 13', 'rank 14', 'rank 15', 'rank 16', 'rank 17', 'rank 18', 'rank 19', 'rank 2', 'rank 20', 'rank 3', 'rank 4', 'rank 5', 'rank 6', 'rank 7', 'rank 8', 'rank 9'], count = 20
...the dimensions of the data used for UMAP are (4424, 20)


Bootstraps:   0%|          | 0/10 [00:00<?, ?it/s]

### visualize external umaps

#### Display UMAPs, color with ground truth v9.0, save as html file

In [41]:
for dataset in umap_tables:
    print(f"Visualizing UMAP embeddings for dataset: {dataset}")
    umap_table = umap_tables[dataset]
    
    label_to_color = "curated_ground_truth_v9.0"  # **choose which annotation column to highlight here** , other choices: cluster_annotation, Protein-level_consensus_annotation
    node_name = umap_table.columns.to_list()[0]

    fig = pu.interaction_umap(
        umap_table,
        node_name=node_name, 
        cluster=label_to_color, opacity=0.35, unlabelled_color="#D0D3D4", unlabelled_opacity=0.1,
        pointsize=6, x="umap_1", y="umap_2",
        categorical=True,
    )
    fig.update_layout(width=1200, height=800)
    # title
    fig.update_layout(    title={
        'text': f"Dataset: {dataset}<br>Annotation: {label_to_color}",
        'x': 0.5
    })

    fig.show()

    # save the figure as an html file
    _output_dir = save_path / dataset / "UMAP" 
    save_name = f"UMAP_interactive_seed={umap_tables_last_seed[dataset]}_groundTruthv9.html"
    pio.write_html(fig, file=os.path.join(_output_dir, save_name), auto_open=False)

Visualizing UMAP embeddings for dataset: DLOPIT2024


Visualizing UMAP embeddings for dataset: DIA-DOMs-2023


Visualizing UMAP embeddings for dataset: hyperLOPITU2OS2018


Visualizing UMAP embeddings for dataset: LOPITDCU2OS2018


Visualizing UMAP embeddings for dataset: itzhak2016stcSILAC


Visualizing UMAP embeddings for dataset: itzhak2016stcSILAC-NOC


Visualizing UMAP embeddings for dataset: BioID2021-NMF
